# Dicoding MLOps Submission 1 - Machine Learning Pipeline with TFX (IMDB Reviews)

- **Nama:** Umar Sani
- **Email:** umarsani@student.uns.ac.id
- **ID Dicoding:** umarsani16

## Import Libraries

In [ ]:
! pip install -U tfx tensorflow_text keras-tuner

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.4/60.4 kB 3.4 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of tensorflow-text to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.7/89.7 kB 4.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 152.0/152.0 kB 9.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.5/43.5 kB 3.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 173.5/173.5 kB 12.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.9/99.9 kB 7.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.8/51.8 kB 3.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... d

In [ ]:
import zipfile
import os, shutil
from google.colab import files
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from keras_tuner.engine import base_tuner

import tensorflow as tf
import tensorflow_text as tf_text
from tfx.components import CsvExampleGen, StatisticsGen, SchemaGen, ExampleValidator, Transform, Trainer, Tuner
from tfx.proto import example_gen_pb2
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext

## Dataset

### Deskripsi

Dataset ini berisi 50.000 ulasan film dari IMDb yang digunakan untuk klasifikasi sentimen biner. Dataset ini terdiri dari 25.000 ulasan positif dan 25.000 ulasan negatif yang dapat digunakan untuk pelatihan dan pengujian algoritma klasifikasi atau deep learning.


**Jumlah Baris dan Kolom:**

Dataset ini memiliki 50.000 baris dan 2 kolom.



**Fitur-Fitur:**

*   `review`: Teks ulasan film.
*   `sentiment`: Label sentimen dari ulasan (positif atau negatif).



**Sumber dataset:**

Dataset ini dapat diunduh dari [Kaggle](https://www.kaggle.com/datasets/lakshmi25npathi/imdb-dataset-of-50k-movie-reviews)

### Unduh Dataset

In [ ]:
! kaggle datasets download -d lakshmi25npathi/imdb-dataset-of-50k-movie-reviews

Dataset URL: https://www.kaggle.com/datasets/lakshmi25npathi/imdb-dataset-of-50k-movie-reviews
License(s): other
 93% 24.0M/25.7M [00:00<00:00, 82.5MB/s]
100% 25.7M/25.7M [00:00<00:00, 79.8MB/s]


In [ ]:
# Ekstrak dataset

def extract(source, destination):
    zip = zipfile.ZipFile(source, "r")
    zip.extractall(destination)
    zip.close()
    print("[SUCCESS] {} berhasil diekstrak ke '{}'".format(os.path.basename(source), destination))

source = "/content/imdb-dataset-of-50k-movie-reviews.zip"
destination = "/content/imdb-dataset-of-50k-movie-reviews"

extract(source, destination)

[SUCCESS] imdb-dataset-of-50k-movie-reviews.zip berhasil diekstrak ke '/content/imdb-dataset-of-50k-movie-reviews'


## Permasalahan

Percobaan ini bertujuan untuk melakukan analisis sentimen terhadap dataset ulasan film IMDB yang terdiri dari 50.000 ulasan. Dataset ini dibagi menjadi dua bagian: 25.000 ulasan untuk pelatihan dan 25.000 ulasan untuk pengujian. Analisis ini akan mengklasifikasikan ulasan menjadi dua kategori utama: positif dan negatif.

## Solusi Machine Learning

Solusi machine learning yang digunakna adalah model deep learning dengan LSTM.

## Metode Pengolahan

### Inisiasi Pipeline Tensorflow Extended

Pertama, inisiasi pipeline TFX dengan mendefinisikan nama pipeline, direktori penyimpanan artifact, dan path untuk metadata. Selain itu, inisiasi InteractiveContext untuk menjalankan komponen TFX secara interaktif.

In [ ]:
# Definisi nama pipeline
PIPELINE_NAME = "umarsani16-pipeline"
SCHEMA_PIPELINE_NAME = "umarsani16-schema"

# Directori root untuk menyimpan artifact
PIPELINE_ROOT = os.path.join('pipelines', PIPELINE_NAME)

# Direktori untuk menyimpan metadata MLMD .
METADATA_PATH = os.path.join('metadata', PIPELINE_NAME, 'metadata.db')

# Direktori untuk menyimpan model serving yang akan dibuat
SERVING_MODEL_DIR = os.path.join('serving_model', PIPELINE_NAME)

# Direktori dataset yang akan digunakan
DATA_ROOT = "/content/imdb-dataset-of-50k-movie-reviews"

In [ ]:
# Inisiasi InteractiveContext
interactive_context = InteractiveContext(pipeline_root=PIPELINE_ROOT)

### Data Ingestion dengan ExampleGen

Kedua, gunakan `CsvExampleGen` untuk mengimpor dataset ulasan film IMDB dari direktori yang telah ditentukan. Dataset ini kemudian dibagi menjadi dua bagian: pelatihan dan evaluasi dengan perbandingan 8:2.

Input dari ExampleGen adalah direktori dataset dan konfigurasi output yang diinginkan, dalam hal ini adalah pembagian dataset training dan evaluation. Sedangkan output dari ExampleGen adalah dataset bertipe data Example.

In [ ]:
output = example_gen_pb2.Output(
    split_config = example_gen_pb2.SplitConfig(splits=[
        example_gen_pb2.SplitConfig.Split(name="train", hash_buckets=8),
        example_gen_pb2.SplitConfig.Split(name="eval", hash_buckets=2)
    ])
)
example_gen = CsvExampleGen(input_base=DATA_ROOT, output_config=output)

In [ ]:
interactive_context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 1
    outputs:
        examples: OutputChannel(artifact_type=Examples, producer_component_id=CsvExampleGen, output_key=examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

### Summary Statistic dengan StatisticGen

Ketiga, gunakan `StatisticsGen` untuk menghasilkan statistik deskriptif dari dataset yang diimpor. Statistik ini membantu dalam memahami distribusi data dan mendeteksi anomali lebih awal.

Input dari `StatisticsGen` adalah artifak bertipe `Examples`. Sedangkan outputnya adalah artifak bertipe `ExampleStatistics`.

In [ ]:
statistics_gen = StatisticsGen(
    examples=example_gen.outputs['examples']
)

interactive_context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 2
    outputs:
        statistics: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=StatisticsGen, output_key=statistics, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [ ]:
interactive_context.show(statistics_gen.outputs["statistics"])

Berdasarkan statistik diatas, dapat dilihat distribusi data dari kedua fitur dataset, `review` dan `sentiment`. Selain itu, ditampilkan juga jumlah record, missing value, unique value, dan statistik lainnya dari setiap fitur.

### Data Schema dengan SchemaGen

Keempat, gunakan `SchemaGen` untuk menghasilkan skema data berdasarkan statistik yang dihasilkan. Skema ini mendefinisikan struktur dan tipe data dari dataset.

Input dari `SchemaGen` adalah artifak bertipe `ExampleStatistics`. Sedangkan outputnya adalah artifak bertipe `Schema`.

In [ ]:
schema_gen = SchemaGen(statistics=statistics_gen.outputs["statistics"])

interactive_context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 3
    outputs:
        schema: OutputChannel(artifact_type=Schema, producer_component_id=SchemaGen, output_key=schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [ ]:
interactive_context.show(schema_gen.outputs["schema"])

Type  Presence Valency       Domain
Feature name                                       
'review'       BYTES  required                    -
'sentiment'   STRING  required          'sentiment'

Values
Domain                             
'sentiment'  'negative', 'positive'

Berdasarkan data schema diatas, dapat dilihat bahwa dataset memiliki dua fitur, yaitu `review` dan `sentiment`. Fitur `review` memiliki tipe data bytes dan wajib ada. Sedangkan fitur `sentiment` memiliki tipe data string dan wajib ada juga. Fitur `sentiment` merupakan fitur kategorikal dengan domain `negative` dan `positive`.


### Identifikasi Anomali dengan ExampleValidator

Kelima, gunakan `ExampleValidator` untuk memvalidasi dataset terhadap skema yang dihasilkan. Proses ini membantu dalam mengidentifikasi dan menangani anomali dalam data.

Input dari `ExampleValidator` adalah artifak bertipe `ExampleStatistics`. Sedangkan outputnya adalah artifak bertipe `ExampleAnomalies`.

In [ ]:
example_validator = ExampleValidator(
    statistics=statistics_gen.outputs['statistics'],
    schema=schema_gen.outputs['schema']
)
interactive_context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 4
    outputs:
        anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=ExampleValidator, output_key=anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [ ]:
interactive_context.show(example_validator.outputs['anomalies'])

Berdasarkan hasil `ExampleValidator` diatas, dapat dilihat bahwa tidak ditemukan anomali pada subset training dan validation.

### Data Preprocessing dengan Transform

Terakhir, gunakan `Transform` untuk melakukan pra-pemrosesan data. Modul `imdb_reviews_transform.py` digunakan untuk mendefinisikan fungsi-fungsi transformasi yang akan dijalankan.

Berikut transformasi yang akan dijalankan:

*   Mengubah semua teks `review` menjadi lowercase
*   Mengubah tipe data `sentiment` menjadi numerik, dengan nilai "positive" menjadi 1 dan "negative" menjadi 0.
*   Mengubah nama kolom dengan suffix "_xf". Seperti berikut: `review_xf` dan `sentiment_xf`.



Input dari `Transform` adalah dataset `Examples`, schema data `Schema`, dan file module yang berisi fungsi `preprocessing_fn`.

Sedangkan output dari `Transform` ada cukup banyak, namun yang utama adalah `transform_graph` dan `transformed_examples`.

In [ ]:
# Mendefinisikan file module transform

TRANSFORM_MODULE_FILE = "imdb_reviews_transform.py"

In [ ]:
%%writefile {TRANSFORM_MODULE_FILE}

import tensorflow as tf
import tensorflow_transform as tft
import tensorflow_text as tf_text

FEATURE_KEY = "review"
LABEL_KEY = "sentiment"

def transformed_name(key):
    return key + "_xf"

def preprocessing_fn(inputs):
    outputs = {}

    outputs[transformed_name(FEATURE_KEY)] = tf.strings.lower(inputs[FEATURE_KEY])

    outputs[transformed_name(LABEL_KEY)] = tf.cast(
        tf.equal(inputs[LABEL_KEY], tf.constant("positive", dtype=tf.string)),
        tf.int64
    )

    return outputs

Writing imdb_reviews_transform.py


In [ ]:
transform = Transform(
    examples=example_gen.outputs['examples'],
    schema=schema_gen.outputs['schema'],
    module_file=TRANSFORM_MODULE_FILE
)

interactive_context.run(transform)

ExecutionResult(
    component_id: Transform
    execution_id: 5
    outputs:
        transform_graph: OutputChannel(artifact_type=TransformGraph, producer_component_id=Transform, output_key=transform_graph, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        transformed_examples: OutputChannel(artifact_type=Examples, producer_component_id=Transform, output_key=transformed_examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        updated_analyzer_cache: OutputChannel(artifact_type=TransformCache, producer_component_id=Transform, output_key=updated_analyzer_cache, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        pre_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=pre_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        pre_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=pre_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=post_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=post_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=Transform, output_key=post_transform_anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

## Arsitektur Model

Setelah dataset dilakukan `Transform`, dataset siap untuk digunakan pada pelatihan model. Pelatihan model pada pipeline TFX menggunakan komponen `Tuner` dan `Trainer`.

### Hyperparameter Tuning dengan Tuner

Komponen `Tuner` digunakan untuk mencari hyperparameter terbaik pada model. `Tuner` memiliki input berupa artifak bertipe `TransformedExamples`, `TransformGraph`, dan `Schema`. Sedangkan outpunya adalah artifak bertipe `BestHyperparameters`. Selain itu, ditentukan juga file tuner module yang mendefinisikan fungsi pelatihan dengan tuning hyperparameter di dalamnya.

Pada percobaan ini, `Tuner` digunakan untuk mencari parameter jumlah neuron LSTM terbaik dari 32 hingga 128. Selain itu mencari learning rate optimizer adam dengan nilai 0.01, 0.001, 0.0001.

File tuner module berisi fungsi-fungsi berikut:

*   `transformed_name`, fungsi ini menambahkan suffix "_xf" pada nama fitur yang telah ditransformasi.
*   `gzip_reader_fn`, fungsi ini digunakan untuk membaca dataset yang terkompresi dalam format GZIP.
*   `input_fn`, fungsi ini digunakan untuk membuat batch dataset yang telah diproses sebelum digunakan untuk pelatihan model.
*   `model_builder`, fungsi digunakan untuk mendefinisikan arsitektur model machine learning yang akan digunakan.
*   `tuner_fn`, fungsi ini merupakan fungsi utama dalam Tuner, fungsi ini akan menjalankan proses hyperparameter tuning.


In [ ]:
# Declare name of module file
TUNER_MODULE_FILE = 'imdb_review_tuner.py'

In [ ]:
%%writefile {TUNER_MODULE_FILE}

from keras_tuner.engine import base_tuner
import keras_tuner as kt
from tensorflow import keras
from tensorflow.keras import layers
from typing import NamedTuple, Dict, Text, Any, List
from tfx.components.trainer.fn_args_utils import FnArgs, DataAccessor
import tensorflow as tf
import tensorflow_transform as tft

# Declare namedtuple field names
TunerFnResult = NamedTuple('TunerFnResult', [('tuner', base_tuner.BaseTuner),
                                             ('fit_kwargs', Dict[Text, Any])])
FEATURE_KEY = "review"
LABEL_KEY = "sentiment"

def transformed_name(key):
    """ Ubah nama fitur hasil transformasi """
    return key + "_xf"

# Callback for the search strategy
stop_early = tf.keras.callbacks.EarlyStopping(monitor='val_accuracy', patience=3)

def gzip_reader_fn(filenames):
    """ Muat dataset reader untuk membaca dataset yang terkompresi """
    return tf.data.TFRecordDataset(filenames, compression_type='GZIP')

def input_fn(file_pattern,
             tf_transform_output,
             num_epochs=None,
             batch_size=32)->tf.data.Dataset:
    """ Ambil fitur hasil transformasi dan buat batch data """

    # Ambil fitur hasil transformasi
    transform_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy())

    # Buat batch data
    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key=transformed_name(LABEL_KEY))

    return dataset

def get_tuner_model(hp):
    """ Buat model machine learning """

    hp_units_1 = hp.Int('units', min_value=32, max_value=128, step=32)
    hp_units_2 = hp.Int('units', min_value=32, max_value=128, step=32)
    hp_learning_rate = hp.Choice('learning_rate', values=[1e-2, 1e-3, 1e-4])

    EMBEDDING_DIM=16
    VOCAB_SIZE = 10000
    SEQUENCE_LENGTH = 100

    vectorize_layer = layers.TextVectorization(
        standardize="lower_and_strip_punctuation",
        max_tokens=VOCAB_SIZE,
        output_mode='int',
        output_sequence_length=SEQUENCE_LENGTH
    )

    inputs = tf.keras.Input(shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string)
    reshaped_narrative = tf.reshape(inputs, [-1])
    x = vectorize_layer(reshaped_narrative)
    x = layers.Embedding(VOCAB_SIZE, EMBEDDING_DIM, name="embedding")(x)

    x = layers.LSTM(hp_units_1, return_sequences=True)(x)
    x = layers.Dropout(0.25)(x)

    x = layers.LSTM(hp_units_2)(x)
    x = layers.Dropout(0.25)(x)

    outputs = layers.Dense(1, activation='sigmoid')(x)

    model = tf.keras.Model(inputs=inputs, outputs = outputs)

    model.compile(
        loss='binary_crossentropy',
        optimizer=keras.optimizers.Adam(learning_rate=hp_learning_rate),
        metrics=[tf.keras.metrics.BinaryAccuracy()]
    )

    model.summary()
    return model

def tuner_fn(fn_args: FnArgs) -> TunerFnResult:
  """ Build the tuner using the KerasTuner API. """

  tuner = kt.Hyperband(get_tuner_model,
                     objective='val_accuracy',
                     max_epochs=10,
                     factor=3,
                     directory=fn_args.working_dir,
                     project_name='kt_hyperband')

  tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

  train_set = input_fn(fn_args.train_files[0], tf_transform_output)
  val_set = input_fn(fn_args.eval_files[0], tf_transform_output)

  return TunerFnResult(
      tuner=tuner,
      fit_kwargs={
          "callbacks":[stop_early],
          'x': train_set,
          'validation_data': val_set,
          'steps_per_epoch': fn_args.train_steps,
          'validation_steps': fn_args.eval_steps
      }
  )

Writing imdb_review_tuner.py


In [ ]:
from tfx.components import Tuner
from tfx.proto import trainer_pb2

tuner = Tuner(
    module_file=os.path.abspath(TUNER_MODULE_FILE),
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=schema_gen.outputs['schema'],
    train_args=trainer_pb2.TrainArgs(splits=['train'], num_steps=100),
    eval_args=trainer_pb2.EvalArgs(splits=['eval'], num_steps=50)
)

interactive_context.run(tuner)

Trial 2 Complete [00h 00m 09s]

Best val_accuracy So Far: None
Total elapsed time: 00h 00m 18s

Search: Running Trial #3

Value             |Best Value So Far |Hyperparameter
128               |64                |units
0.01              |0.001             |learning_rate
2                 |2                 |tuner/epochs
0                 |0                 |tuner/initial_epoch
2                 |2                 |tuner/bracket
0                 |0                 |tuner/round

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 review_xf (InputLayer)      [(None, 1)]               0         
                                                                 
 tf.reshape (TFOpLambda)     (None,)                   0         
                                                                 
 text_vectorization (TextVe  (None, 100)               0         
 ctorization)                           

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/engine/base_tuner.py", line 274, in _try_run_and_update_trial
    self._run_and_update_trial(trial, *fit_args, **fit_kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/engine/base_tuner.py", line 239, in _run_and_update_trial
    results = self.run_trial(trial, *fit_args, **fit_kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/tuners/hyperband.py", line 427, in run_trial
    return super().run_trial(trial, *fit_args, **fit_kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/engine/tuner.py", line 314, in run_trial
    obj_value = self._build_and_fit_model(trial, *args, **copied_kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/engine/tuner.py", line 233, in _build_and_fit_model
    results = self.hypermodel.fit(hp, model, *args, **kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/eng

RuntimeError: Number of consecutive failures exceeded the limit of 3.
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/engine/base_tuner.py", line 274, in _try_run_and_update_trial
    self._run_and_update_trial(trial, *fit_args, **fit_kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/engine/base_tuner.py", line 239, in _run_and_update_trial
    results = self.run_trial(trial, *fit_args, **fit_kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/tuners/hyperband.py", line 427, in run_trial
    return super().run_trial(trial, *fit_args, **fit_kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/engine/tuner.py", line 314, in run_trial
    obj_value = self._build_and_fit_model(trial, *args, **copied_kwargs)
  File "/usr/local/lib/python3.10/dist-packages/keras_tuner/src/engine/tuner.py", line 233, in _build_and_fit_model
    results = self.hypermodel.fit(hp, model, *args, **kwarg

Komponen `Tuner` akan menghasilkan best hyperparameter. Hyperparater tersebut akan diinputkan ke dalam komponen `Trainer`.

**Catatan**:

Saya mengalami error pada saat running `Tuner`



```
Table not initialized.
     [[{{node model/text_vectorization/string_lookup/None_Lookup/LookupTableFindV2}}]] [Op:__inference_train_function_206772]
```

Mungkin Kakak Reviewer dapat membantu saya dalam menangani hal tersebut.

### Training Model dengan Trainer

Komponen `Trainer` digunakan untuk melakukan pelatihan dan validasi model. `Trainer` memiliki input berupa artifak `TransformedExamples` dan `TransformGraph` dari `Transform`, serta `Schema` dari `SchemaGen`. Selain itu, ditentukan juga file trainer module yang mendefinisikan fungsi pelatihan yang akan dijalankan dan konfigurasi training dan validation. Sedangkan outputnya adalah artifak bertipe `Model`, yang berisi model machine learning yang telah dilatih.

File trainer module berisi fungsi-fungsi berikut:

*   `transformed_name`, fungsi ini menambahkan suffix "_xf" pada nama fitur yang telah ditransformasi.
*   `gzip_reader_fn`, fungsi ini digunakan untuk membaca dataset yang terkompresi dalam format GZIP.
*   `input_fn`, fungsi ini digunakan untuk membuat batch dataset yang telah diproses sebelum digunakan untuk pelatihan model.
*   `model_builder`, fungsi digunakan untuk mendefinisikan arsitektur model machine learning yang akan digunakan.
*   `run_fn`, fungsi ini merupakan fungsi utama dalam Trainer, fungsi ini akan menjalankan proses pelatihan dan evaluasi model, kemudian menyimpan modelnya.



In [ ]:
# Mendefinisikan file module trainer
TRAINER_MODULE_FILE = "imdb_review_trainer.py"

In [ ]:
%%writefile {TRAINER_MODULE_FILE}

import tensorflow as tf
import tensorflow_transform as tft
from tensorflow.keras import layers
import os
import tensorflow_hub as hub
from tfx.components.trainer.fn_args_utils import FnArgs

FEATURE_KEY = "review"
LABEL_KEY = "sentiment"

def transformed_name(key):
    """ Ubah nama fitur hasil transformasi """
    return key + "_xf"

def gzip_reader_fn(filenames):
    """ Muat dataset reader untuk membaca dataset yang terkompresi """
    return tf.data.TFRecordDataset(filenames, compression_type='GZIP')

def input_fn(file_pattern,
             tf_transform_output,
             num_epochs,
             batch_size=64)->tf.data.Dataset:
    """ Ambil fitur hasil transformasi dan buat batch data """

    # Ambil fitur hasil transformasi
    transform_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy())

    # Buat batch data
    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key = transformed_name(LABEL_KEY))
    return dataset

EMBEDDING_DIM=16
VOCAB_SIZE = 10000
SEQUENCE_LENGTH = 100

vectorize_layer = layers.TextVectorization(
    standardize="lower_and_strip_punctuation",
    max_tokens=VOCAB_SIZE,
    output_mode='int',
    output_sequence_length=SEQUENCE_LENGTH
)

def model_builder():
    """ Buat model machine learning """

    inputs = tf.keras.Input(shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string)
    reshaped_narrative = tf.reshape(inputs, [-1])
    x = vectorize_layer(reshaped_narrative)
    x = layers.Embedding(VOCAB_SIZE, EMBEDDING_DIM, name="embedding")(x)
    x = layers.LSTM(100, return_sequences=True)(x)
    x = layers.Dropout(0.25)(x)
    x = layers.LSTM(100)(x)
    x = layers.Dropout(0.25)(x)
    outputs = layers.Dense(1, activation='sigmoid')(x)

    model = tf.keras.Model(inputs=inputs, outputs=outputs)

    model.compile(
        loss='binary_crossentropy',
        optimizer='rmsprop',
        metrics=[tf.keras.metrics.BinaryAccuracy()]
    )

    model.summary()
    return model

def _get_serve_tf_examples_fn(model, tf_transform_output):

    model.tft_layer = tf_transform_output.transform_features_layer()

    @tf.function
    def serve_tf_examples_fn(serialized_tf_examples):

        feature_spec = tf_transform_output.raw_feature_spec()

        feature_spec.pop(LABEL_KEY)

        parsed_features = tf.io.parse_example(serialized_tf_examples, feature_spec)

        transformed_features = model.tft_layer(parsed_features)

        return model(transformed_features)

    return serve_tf_examples_fn

def run_fn(fn_args: FnArgs) -> None:

    log_dir = os.path.join(os.path.dirname(fn_args.serving_model_dir), 'logs')

    tensorboard_callback = tf.keras.callbacks.TensorBoard(
        log_dir = log_dir, update_freq='batch'
    )

    es = tf.keras.callbacks.EarlyStopping(monitor='val_binary_accuracy', mode='max', verbose=1, patience=10)
    mc = tf.keras.callbacks.ModelCheckpoint(fn_args.serving_model_dir, monitor='val_binary_accuracy', mode='max', verbose=1, save_best_only=True)

    tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

    train_set = input_fn(fn_args.train_files, tf_transform_output, 10)
    val_set = input_fn(fn_args.eval_files, tf_transform_output, 10)
    vectorize_layer.adapt(
        [j[0].numpy()[0] for j in [
            i[0][transformed_name(FEATURE_KEY)]
                for i in list(train_set)]])

    model = model_builder()

    model.fit(x = train_set,
            validation_data = val_set,
            callbacks = [tensorboard_callback, es, mc],
            steps_per_epoch = 1000,
            validation_steps= 1000,
            epochs=10)

    signatures = {
        'serving_default':
        _get_serve_tf_examples_fn(model, tf_transform_output).get_concrete_function(
                                    tf.TensorSpec(
                                    shape=[None],
                                    dtype=tf.string,
                                    name='review'))
    }

    model.save(fn_args.serving_model_dir, save_format='tf', signatures=signatures)

Writing imdb_review_trainer.py


In [ ]:
from tfx.components import Tuner
from tfx.proto import trainer_pb2

trainer  = Trainer(
    module_file=os.path.abspath(TRAINER_MODULE_FILE),
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=schema_gen.outputs['schema'],
    train_args=trainer_pb2.TrainArgs(splits=['train']),
    eval_args=trainer_pb2.EvalArgs(splits=['eval'])
)

interactive_context.run(trainer)

Instructions for updating:
Use `tf.data.Dataset.map(tf.io.parse_example(...))` instead.


Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 review_xf (InputLayer)      [(None, 1)]               0         
                                                                 
 tf.reshape (TFOpLambda)     (None,)                   0         
                                                                 
 text_vectorization (TextVe  (None, 100)               0         
 ctorization)                                                    
                                                                 
 embedding (Embedding)       (None, 100, 16)           160000    
                                                                 
 lstm (LSTM)                 (None, 100, 100)          46800     
                                                                 
 dropout (Dropout)           (None, 100, 100)          0         
                                                             


Epoch 7: val_binary_accuracy did not improve from 0.83675
1000/1000 [==============================] - 240s 240ms/step - loss: 0.2626 - binary_accuracy: 0.8962 - val_loss: 0.4414 - val_binary_accuracy: 0.8332


ExecutionResult(
    component_id: Trainer
    execution_id: 6
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Trainer, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        model_run: OutputChannel(artifact_type=ModelRun, producer_component_id=Trainer, output_key=model_run, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

## Metrik Evaluasi

Setelah model telah dilatih, tahap selanjutnya adalah analisis dan validasi model. Analisis dan validasi model akan dilakukan dengan menggunakan komponen `Resolver` dan `Evaluator`, yang akan dibahas pada bab selanjutnya.

Metrik evaluasi yang digunakan adalah akurasi, presisi, recall, dan F1-score.

*   Akurasi mengukur proporsi prediksi yang benar dari keseluruhan prediksi:

$$ \text{Akurasi} = \frac{TP + TN}{TP + TN + FP + FN} $$

*   Presisi mengukur proporsi prediksi positif yang benar dari semua prediksi positif: $$ \text{Presisi} = \frac{TP}{TP + FP} $$

*   Recall (Sensitivitas) mengukur proporsi prediksi positif yang benar dari semua kasus positif yang sebenarnya:

$$ \text{Recall} = \frac{TP}{TP + FN} $$

*   F1-Score adalah rata-rata harmonis dari presisi dan recall:

$$ \text{F1-Score} = 2 \times \frac{\text{Presisi} \times \text{Recall}}{\text{Presisi} + \text{Recall}} $$


## Performa Model

### Tentukan Baseline Model dengan Resolver

Untuk melakukan analisis dan validasi model, baseline model perlu ditentukan terlebih dahulu. Baseline model adalah model referensi yang digunakan sebagai titik awal atau standar untuk membandingkan performa model baru. Baseline model bisa didapat dengan komponen `Resolver`.

Komponen `Resolver` memiliki input berupa artifak bertipe bertipe `Model` dan `ModelBlessing` dari eksekusi `Trainer` sebelumnya. Sedangkan outputnya adalah artifak bertipe `Model`, yang merupakan baseline model, dan `ModelBlessing`.

In [ ]:
from tfx.dsl.components.common.resolver import Resolver
from tfx.dsl.input_resolution.strategies.latest_blessed_model_strategy import LatestBlessedModelStrategy
from tfx.types import Channel
from tfx.types.standard_artifacts import Model, ModelBlessing

model_resolver = Resolver(
    strategy_class=LatestBlessedModelStrategy,
    model=Channel(type=Model),
    model_blessing=Channel(type=ModelBlessing)
).with_id('Latest_blessed_model_resolver')

interactive_context.run(model_resolver)

ExecutionResult(
    component_id: Latest_blessed_model_resolver
    execution_id: 7
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Latest_blessed_model_resolver, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        model_blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Latest_blessed_model_resolver, output_key=model_blessing, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

### Evaluasi Model dengan Evaluator

`Evaluator` digunakan untuk mengevaluasi model yang dipilih oleh `Resolver`. `Evaluator` menggunakan berbagai metrik seperti akurasi, presisi, recall, F1-score, dan AUC-ROC untuk menilai performa model.

`Evaluator` memiliki input berupa artifak bertipe `TransformedExamples` dari `Transform`, `Model` dari `Trainer`, baseline model `Model` dari `Resolver`, dan konfigurasi evaluasi yang akan dijalankan. Sedangkan outpunya adalah artifak bertipe `Evaluation`, yang berisi hasil evaluasi model.

Pada `eval_config` atau konfigurasi evaluasi yang akan dijalankan, ditentukan kolom label, slicing, dan metrik evaluasi yang ingin digunakan. Dalam percobaan ini metrik yang digunakan yaitu jumlah data, precision, recall, f1-score, dan akurasi.

In [ ]:
import tensorflow_model_analysis as tfma

eval_config = tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key='sentiment_xf')],
    slicing_specs=[tfma.SlicingSpec()],
    metrics_specs=[
        tfma.MetricsSpec(metrics=[
            tfma.MetricConfig(class_name='ExampleCount'),
            tfma.MetricConfig(class_name='Precision'),
            tfma.MetricConfig(class_name='Recall'),
            tfma.MetricConfig(class_name='F1Score'),
            tfma.MetricConfig(class_name='BinaryAccuracy',
                threshold=tfma.MetricThreshold(
                    value_threshold=tfma.GenericValueThreshold(
                        lower_bound={'value':0.5}),
                    change_threshold=tfma.GenericChangeThreshold(
                        direction=tfma.MetricDirection.HIGHER_IS_BETTER,
                        absolute={'value':0.0001})
                    )
            )
        ])
    ]
)

In [ ]:
from tfx.components import Evaluator
evaluator = Evaluator(
    examples=transform.outputs['transformed_examples'],
    model=trainer.outputs['model'],
    baseline_model=model_resolver.outputs['model'],
    eval_config=eval_config)

interactive_context.run(evaluator)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


ExecutionResult(
    component_id: Evaluator
    execution_id: 8
    outputs:
        evaluation: OutputChannel(artifact_type=ModelEvaluation, producer_component_id=Evaluator, output_key=evaluation, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Evaluator, output_key=blessing, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [ ]:
eval_result = evaluator.outputs['evaluation'].get()[0].uri
tfma_result = tfma.load_eval_result(eval_result)
tfma.view.render_slicing_metrics(tfma_result)
tfma.addons.fairness.view.widget_view.render_fairness_indicator(
    tfma_result
)

Berdasarkan data hasil evaluasi diatas, dapat dilihat bahwa model mendapatkan hasil berikut:

*   jumlah data: 9956
*   akurasi: 0.83337
*   loss: 0.44146
*   precision: 0.88048
*   recall: 0.77521
*   f1-score: 0.82450



## Deployment dengan Pusher

Terakhir, gunakan komponen `Pusher` untuk men-deploy model yang siap pakai.

Komponen `Pusher` memiliki input berupa artifak bertipe `Model` hasil dari `Trainer` dan `ModelBlessing` hasil dari `Resolver`. Sedangkan outputnya adalah `PushedModel`, yang merupakan deployment model yang siap digunakan pada lingkungan produksi.

In [ ]:
from tfx.components import Pusher
from tfx.proto import pusher_pb2

pusher = Pusher(
model=trainer.outputs['model'],
model_blessing=evaluator.outputs['blessing'],
push_destination=pusher_pb2.PushDestination(
    filesystem=pusher_pb2.PushDestination.Filesystem(
        base_directory='serving_model_dir/imdb-review-model'))

)

interactive_context.run(pusher)

ExecutionResult(
    component_id: Pusher
    execution_id: 9
    outputs:
        pushed_model: OutputChannel(artifact_type=PushedModel, producer_component_id=Pusher, output_key=pushed_model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

Unduh file model dan pipeline ke lokal

In [ ]:
def compress(source, destination):
    with zipfile.ZipFile(destination, 'w', zipfile.ZIP_DEFLATED) as zipf:
        for root, dirs, files in os.walk(source):
            for file in files:
                file_path = os.path.join(root, file)
                zipf.write(file_path, os.path.relpath(file_path, source))
    print("[SUCCESS] {} berhasil dikompres ke '{}'".format(os.path.basename(source), destination))

In [ ]:
source = "/content/serving_model_dir/imdb-review-model/1732276359"
destination = "/content/imdb-review-model.zip"

compress(source, destination)

source = "/content/pipelines/umarsani16-pipeline"
destination = "/content/umarsani16-pipeline.zip"

compress(source, destination)

[SUCCESS] 1732276359 berhasil dikompres ke '/content/imdb-review-model.zip'
[SUCCESS] umarsani16-pipeline berhasil dikompres ke '/content/umarsani16-pipeline.zip'


In [ ]:
files.download("/content/imdb-review-model.zip")
files.download("/content/umarsani16-pipeline.zip")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>